In [94]:
import os, sys, json, datetime, re  # Provides OS-dependent functionality, system-specific parameters, JSON handling, and date/time manipulation
import pandas as pd             # Provides data structures and data analysis tools
import numpy as np              # Supports large, multi-dimensional arrays and matrices
import requests
import time
from tqdm import tqdm
import urllib3
urllib3.disable_warnings(urllib3.exceptions.InsecureRequestWarning)
from bs4 import BeautifulSoup
from lxml import etree, html
from selenium import webdriver
from selenium.webdriver.common.keys import Keys

from selenium.webdriver.common.by import By
from selenium.webdriver.common import keys
from selenium.webdriver.chrome.service import Service
from selenium.webdriver.chrome.options import Options
from selenium.webdriver.common.action_chains import ActionChains
import time
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC

from selenium import webdriver
from selenium.webdriver.chrome.service import Service as ChromeService
from webdriver_manager.chrome import ChromeDriverManager

In [6]:
url = "https://vademocrats.org/localities/"


In [72]:
import geonamescache
gc = geonamescache.GeonamesCache()
cities = gc.get_cities()



print(cities)
cities_df = cities[cities['countrycode'] == 'US']

{'3040051': {'geonameid': 3040051, 'name': 'les Escaldes', 'latitude': 42.50729, 'longitude': 1.53414, 'countrycode': 'AD', 'population': 15853, 'timezone': 'Europe/Andorra', 'admin1code': '08', 'alternatenames': ["Ehskal'des-Ehndzhordani", 'Escaldes', 'Escaldes-Engordany', 'Les Escaldes', 'esukarudesu=engorudani jiao qu', 'lai sai si ka er de-en ge er da', 'Эскальдес-Энджордани', 'エスカルデス＝エンゴルダニ教区', '萊塞斯卡爾德-恩戈爾達', '萊塞斯卡爾德－恩戈爾達']}, '3041563': {'geonameid': 3041563, 'name': 'Andorra la Vella', 'latitude': 42.50779, 'longitude': 1.52109, 'countrycode': 'AD', 'population': 20430, 'timezone': 'Europe/Andorra', 'admin1code': '07', 'alternatenames': ['ALV', 'Ando-la-Vyey', 'Andora', 'Andora la Vela', 'Andora la Velja', "Andora lja Vehl'ja", 'Andoro Malnova', 'Andorra', 'Andorra Tuan', 'Andorra a Vella', 'Andorra la Biella', 'Andorra la Vella', 'Andorra la Vielha', 'Andorra-a-Velha', "Andorra-la-Vel'ja", 'Andorra-la-Vielye', 'Andorre-la-Vieille', 'Andò-la-Vyèy', 'Andòrra la Vièlha', 'an dao er

KeyError: 'countrycode'

In [ ]:

va_city_names = []
for city_id, city_info in cities.items():
    
    if city_info['countrycode'] == 'US' and city_info['admin1code'] == 'VA':
        # print(city_id, city_info)  
        print(type(city_info))
        va_city_names.append(city_info['name'])

        # print(city_info.to_string())
        # print(city_info['name'], city_info['latitude'], city_info['longitude'])
        # break



In [ ]:
webdriver_path = r"C:\Users\clutz\hunt_env\chrome driver\chromedriver-win64\chromedriver.exe"
chrome_options = Options()

# chrome_options.add_argument("--headless")  # Run in headless mode (no GUI)
# Set up WebDriver service
service = Service(webdriver_path)
#call on driver and get data
driver = webdriver.Chrome(service=ChromeService(ChromeDriverManager().install()), options=chrome_options)


In [107]:
print(*va_city_names, sep = ' | ')

Fort Hunt | Alexandria | Annandale | Arlington | Ashburn | Baileys Crossroads | Blacksburg | Bon Air | Bristol | Buckhall | Burke | Cave Spring | Centreville | Chantilly | Charlottesville | Cherry Hill | Chesapeake | Chester | Christiansburg | Colonial Heights | Culpeper | Dale City | Danville | East Hampton | Fairfax | Franconia | Fredericksburg | Front Royal | Great Falls | Hampton | Harrisonburg | Herndon | Highland Springs | Hopewell | Hybla Valley | Idylwood | Lake Ridge | Laurel | Leesburg | Lincolnia | Linton Hall | Lorton | Lynchburg | Manassas | Manassas Park | McLean | Mechanicsville | Merrifield | Montclair | Newport News | Norfolk | Oakton | Petersburg | Portsmouth | Portsmouth Heights | Radford | Reston | Richmond | Roanoke | Rose Hill | Salem | Short Pump | South Riding | South Suffolk | Springfield | Staunton | Sterling | Sudley | Suffolk | Tuckahoe | Tysons Corner | Vienna | Virginia Beach | Waynesboro | West Lynchburg | West Springfield | Williamsburg | Winchester | Wo

In [112]:

page_url = r"https://www.vpap.org/electionresults/20241105/local/"
driver.get(page_url)


#site-canvas > main > article > div.container > ul > div:nth-child(1)
element = driver.find_element(By.XPATH, '//*[@id="local-autocomplete-3kq5-input"]')
element.click()

for name in va_city_names:
    input_keys = str(name)[:-8]
    element.send_keys(input_keys)

    elements = driver.find_elements(By.XPATH, "//*[starts-with(@class, 'gsc')]")

    print(len(elements))
    for e in elements:
        print(e.text)
#local-autocomplete-3kq5-listitem-2845
    break


0


In [ ]:

WebDriverWait(2, 20)
element.send_keys(Keys.ARROW_DOWN)


# END

In [ ]:

#b soup line
html_from_page = driver.page_source
soup = BeautifulSoup(html_from_page, 'html.parser')
ul_tag = soup.find("ul", class_="county-list")
type(ul_tag.contents)
# for div in ul_tag.contents:
#     if 'String' in str(type(div)):
#         continue
#     else:
        
#         print(type(div))
#         print(len(div.text))

link_dict = {}

for child in ul_tag.children:
    if 'String' in str(type(child)):
        continue    
    
    # print(child)
    links = child.find_all(href=True)
    for link in links:

        # print(link.text)
        # print(type(link))
        link_exp = link.get('href')
        co_name = link.text
        link_dict[co_name] = link_exp

In [ ]:
co_web_links = {}
co_no_website = []
for k,v in link_dict.items():
    print(k)
    driver.get(v)
    html_from_page = driver.page_source
    co_soup = BeautifulSoup(html_from_page, 'html.parser')
    
    co_ul_tag = co_soup.find("div", class_="link-holder text-center")
    if not co_ul_tag:
        print(type(co_ul_tag))
        print('probably is a nonetype result')
        co_no_website.append(k)
        continue
    for c in co_ul_tag.children:
        
        if 'String' in str(type(c)) or 'Facebook' in str(c):
            continue
        
        elif 'Website' in str(c):
            web_link = c.get('href')
            co_web_links[k] = web_link
        else:
            continue
        
        
    # print(co_link_tag)
    
    # break


In [ ]:
co_web_links

In [ ]:


soup.css.select("title")



element = driver.find_element(By.CLASS_NAME, "county-list")
print(element.tag_name)
print(element.get_attribute('class'))
# soup = BeautifulSoup(html_from_page, 'html.parser')

# links = soup.find_all("a", {"class": "list-group-item list-group-item-action filteredGroup searchable"})
#site-canvas > main > article > div.container > ul